In [1]:
import sys
import os
sys.path.append(os.path.abspath(os.path.join(os.getcwd(), '../..')))

# Path Configuration
from tools.preprocess import *

# Processing context
trait = "Prostate_Cancer"
cohort = "GSE209954"

# Input paths
in_trait_dir = "../../input/GEO/Prostate_Cancer"
in_cohort_dir = "../../input/GEO/Prostate_Cancer/GSE209954"

# Output paths
out_data_file = "../../output/preprocess/Prostate_Cancer/GSE209954.csv"
out_gene_data_file = "../../output/preprocess/Prostate_Cancer/gene_data/GSE209954.csv"
out_clinical_data_file = "../../output/preprocess/Prostate_Cancer/clinical_data/GSE209954.csv"
json_path = "../../output/preprocess/Prostate_Cancer/cohort_info.json"


### Step 1: Initial Data Loading

In [2]:
from tools.preprocess import *
# 1. Identify the paths to the SOFT file and the matrix file
soft_file, matrix_file = geo_get_relevant_filepaths(in_cohort_dir)

# 2. Read the matrix file to obtain background information and sample characteristics data
background_prefixes = ['!Series_title', '!Series_summary', '!Series_overall_design']
clinical_prefixes = ['!Sample_geo_accession', '!Sample_characteristics_ch1']
background_info, clinical_data = get_background_and_clinical_data(matrix_file, background_prefixes, clinical_prefixes)

# 3. Obtain the sample characteristics dictionary from the clinical dataframe
sample_characteristics_dict = get_unique_values_by_row(clinical_data)

# 4. Explicitly print out all the background information and the sample characteristics dictionary
print("Background Information:")
print(background_info)
print("Sample Characteristics Dictionary:")
print(sample_characteristics_dict)


Background Information:
!Series_title	"Genomic testing in early localized prostate cancer may define subsets of African Americans with aggressive disease—a prospective study"
!Series_summary	"Gene expression study of the VANDAAM Phase II clinical trial"
!Series_overall_design	"Prospective analysis of 226 tumor transcriptomes from VANDAAM."
Sample Characteristics Dictionary:
{0: ['tissue: prostate cancer'], 1: ['primary gleason: 3', 'primary gleason: 4'], 2: ['secondary gleason: 3', 'secondary gleason: 4'], 3: ['pre-treatment psa (ng/ml): 4.1', 'pre-treatment psa (ng/ml): 11.23', 'pre-treatment psa (ng/ml): 7.3', 'pre-treatment psa (ng/ml): 6.09', 'pre-treatment psa (ng/ml): 8.38', 'pre-treatment psa (ng/ml): 6.79', 'pre-treatment psa (ng/ml): 7.8', 'pre-treatment psa (ng/ml): 3.7', 'pre-treatment psa (ng/ml): 8.15', 'pre-treatment psa (ng/ml): 4.9', 'pre-treatment psa (ng/ml): 7.38', 'pre-treatment psa (ng/ml): 11.38', 'pre-treatment psa (ng/ml): 2.57', 'pre-treatment psa (ng/ml): 9.53

### Step 2: Dataset Analysis and Clinical Feature Extraction

In [3]:
import pandas as pd
import os
import json
from typing import Optional, Callable, Dict, Any

# 1. Determine gene expression data availability
is_gene_available = True  # Based on background info, this appears to be gene expression data

# 2. Variable availability and data type conversion

# 2.1 Data Availability
# For trait (prostate cancer) - from row 5, we can use race as a proxy for trait
# The dataset focuses on African Americans vs non-African Americans with prostate cancer
trait_row = 5  # race: AAM vs NAAM

# For age - row 4 contains age information
age_row = 4

# For gender - not explicitly stated, but from background info, this is a prostate cancer study
# Prostate cancer only affects biological males, so we can infer all samples are male
gender_row = None  # Not available as a variable since all samples would be male

# 2.2 Data Type Conversion
def convert_trait(value):
    # Add type checking to handle non-string inputs
    if not isinstance(value, str):
        return None
    # Convert race to binary format (1 for AAM - African American Males, 0 for NAAM - Non-African American Males)
    if ':' in value:
        race = value.split(':')[1].strip()
        if race == 'AAM':
            return 1
        elif race == 'NAAM':
            return 0
    return None

def convert_age(value):
    # Add type checking
    if not isinstance(value, str):
        return None
    # Extract age value after the colon and convert to float for continuous variable
    try:
        # Extract number after "age: "
        age_str = value.split(':')[1].strip()
        return float(age_str)
    except (IndexError, ValueError):
        return None

def convert_gender(value):
    # This function is not used but included for completeness
    # For prostate cancer studies, all subjects would be male (1)
    return 1

# 3. Save metadata
is_trait_available = trait_row is not None
initial_validation = validate_and_save_cohort_info(
    is_final=False, 
    cohort=cohort, 
    info_path=json_path, 
    is_gene_available=is_gene_available, 
    is_trait_available=is_trait_available
)

# 4. Clinical Feature Extraction
if trait_row is not None:
    # Use the sample characteristics dictionary directly
    # Create a clinical DataFrame suitable for processing
    
    # Recreate the sample characteristics as a DataFrame
    sample_chars = {
        0: ['tissue: prostate cancer'], 
        1: ['primary gleason: 3', 'primary gleason: 4'], 
        2: ['secondary gleason: 3', 'secondary gleason: 4'], 
        3: ['pre-treatment psa (ng/ml): 4.1', 'pre-treatment psa (ng/ml): 11.23', 'pre-treatment psa (ng/ml): 7.3', 
            'pre-treatment psa (ng/ml): 6.09', 'pre-treatment psa (ng/ml): 8.38', 'pre-treatment psa (ng/ml): 6.79', 
            'pre-treatment psa (ng/ml): 7.8', 'pre-treatment psa (ng/ml): 3.7', 'pre-treatment psa (ng/ml): 8.15', 
            'pre-treatment psa (ng/ml): 4.9', 'pre-treatment psa (ng/ml): 7.38', 'pre-treatment psa (ng/ml): 11.38', 
            'pre-treatment psa (ng/ml): 2.57', 'pre-treatment psa (ng/ml): 9.53', 'pre-treatment psa (ng/ml): 3.8', 
            'pre-treatment psa (ng/ml): 5.37', 'pre-treatment psa (ng/ml): 13.14', 'pre-treatment psa (ng/ml): 2.22', 
            'pre-treatment psa (ng/ml): 9.39', 'pre-treatment psa (ng/ml): 5.51', 'pre-treatment psa (ng/ml): 7.02', 
            'pre-treatment psa (ng/ml): 10.9', 'pre-treatment psa (ng/ml): 5.72', 'pre-treatment psa (ng/ml): 7.69', 
            'pre-treatment psa (ng/ml): 10.06', 'pre-treatment psa (ng/ml): 9.7', 'pre-treatment psa (ng/ml): 10.5', 
            'pre-treatment psa (ng/ml): 5.89', 'pre-treatment psa (ng/ml): 4.3', 'pre-treatment psa (ng/ml): 7.4'], 
        4: ['age: 45', 'age: 67', 'age: 47', 'age: 68', 'age: 70', 'age: 61', 'age: 62', 'age: 51', 'age: 69', 
            'age: 65', 'age: 74', 'age: 71', 'age: 58', 'age: 64', 'age: 55', 'age: 59', 'age: 60', 'age: 56', 
            'age: 75', 'age: 72', 'age: 54', 'age: 76', 'age: 66', 'age: 49', 'age: 46', 'age: 63', 'age: 73', 
            'age: 57', 'age: 52', 'age: 50'], 
        5: ['race: AAM', 'race: NAAM']
    }
    
    # Determine the number of samples from the longest list
    max_samples = max(len(values) for values in sample_chars.values())
    
    # Create a DataFrame with proper dimensions, initializing all cells to None
    clinical_data = pd.DataFrame(index=range(len(sample_chars)), columns=[f'Sample_{i+1}' for i in range(max_samples)])
    
    # Fill in the data
    for row, values in sample_chars.items():
        for i, value in enumerate(values):
            clinical_data.iloc[row, i] = value
    
    # Extract clinical features
    selected_clinical = geo_select_clinical_features(
        clinical_df=clinical_data,
        trait=trait,
        trait_row=trait_row,
        convert_trait=convert_trait,
        age_row=age_row,
        convert_age=convert_age,
        gender_row=gender_row,
        convert_gender=convert_gender
    )
    
    # Preview the dataframe
    preview = preview_df(selected_clinical)
    print("Preview of selected clinical features:")
    print(preview)
    
    # Save to CSV
    os.makedirs(os.path.dirname(out_clinical_data_file), exist_ok=True)
    selected_clinical.to_csv(out_clinical_data_file, index=False)
    print(f"Clinical data saved to {out_clinical_data_file}")


Preview of selected clinical features:
{'Sample_1': [1.0, 45.0], 'Sample_2': [0.0, 67.0], 'Sample_3': [nan, 47.0], 'Sample_4': [nan, 68.0], 'Sample_5': [nan, 70.0], 'Sample_6': [nan, 61.0], 'Sample_7': [nan, 62.0], 'Sample_8': [nan, 51.0], 'Sample_9': [nan, 69.0], 'Sample_10': [nan, 65.0], 'Sample_11': [nan, 74.0], 'Sample_12': [nan, 71.0], 'Sample_13': [nan, 58.0], 'Sample_14': [nan, 64.0], 'Sample_15': [nan, 55.0], 'Sample_16': [nan, 59.0], 'Sample_17': [nan, 60.0], 'Sample_18': [nan, 56.0], 'Sample_19': [nan, 75.0], 'Sample_20': [nan, 72.0], 'Sample_21': [nan, 54.0], 'Sample_22': [nan, 76.0], 'Sample_23': [nan, 66.0], 'Sample_24': [nan, 49.0], 'Sample_25': [nan, 46.0], 'Sample_26': [nan, 63.0], 'Sample_27': [nan, 73.0], 'Sample_28': [nan, 57.0], 'Sample_29': [nan, 52.0], 'Sample_30': [nan, 50.0]}
Clinical data saved to ../../output/preprocess/Prostate_Cancer/clinical_data/GSE209954.csv


### Step 3: Gene Data Extraction

In [4]:
# 1. Get the SOFT and matrix file paths again 
soft_file, matrix_file = geo_get_relevant_filepaths(in_cohort_dir)
print(f"Matrix file found: {matrix_file}")

# 2. Use the get_genetic_data function from the library to get the gene_data
try:
    gene_data = get_genetic_data(matrix_file)
    print(f"Gene data shape: {gene_data.shape}")
    
    # 3. Print the first 20 row IDs (gene or probe identifiers)
    print("First 20 gene/probe identifiers:")
    print(gene_data.index[:20])
except Exception as e:
    print(f"Error extracting gene data: {e}")


Matrix file found: ../../input/GEO/Prostate_Cancer/GSE209954/GSE209954_series_matrix.txt.gz


Gene data shape: (22011, 226)
First 20 gene/probe identifiers:
Index(['2315554', '2315633', '2315674', '2315739', '2315894', '2315918',
       '2315951', '2316218', '2316245', '2316379', '2316558', '2316605',
       '2316746', '2316905', '2316953', '2317246', '2317317', '2317434',
       '2317472', '2317512'],
      dtype='object', name='ID')


### Step 4: Gene Identifier Review

In [5]:
# Looking at the gene identifiers '2315554', '2315633', etc.
# These appear to be numeric identifiers, likely probe IDs from a microarray platform
# They are not standard human gene symbols (like BRCA1, TP53, etc.)
# Therefore, we'll need to map these identifiers to standard gene symbols

requires_gene_mapping = True


### Step 5: Gene Annotation

In [6]:
# 1. Use the 'get_gene_annotation' function from the library to get gene annotation data from the SOFT file.
gene_annotation = get_gene_annotation(soft_file)

# 2. Analyze the gene annotation dataframe to identify which columns contain the gene identifiers and gene symbols
print("\nGene annotation preview:")
print(f"Columns in gene annotation: {gene_annotation.columns.tolist()}")
print(preview_df(gene_annotation, n=5))

# Let's look for platform information in the SOFT file to understand the annotation better
print("\nSearching for platform information in SOFT file:")
with gzip.open(soft_file, 'rt') as f:
    for i, line in enumerate(f):
        if '!Series_platform_id' in line:
            print(line.strip())
            break
        if i > 100:  # Limit search to first 100 lines
            print("Platform ID not found in first 100 lines")
            break

# Check if the SOFT file includes any reference to gene symbols
print("\nSearching for gene symbol information in SOFT file:")
with gzip.open(soft_file, 'rt') as f:
    gene_symbol_lines = []
    for i, line in enumerate(f):
        if 'GENE_SYMBOL' in line or 'gene_symbol' in line.lower() or 'symbol' in line.lower():
            gene_symbol_lines.append(line.strip())
        if i > 1000 and len(gene_symbol_lines) > 0:  # Limit search but ensure we found something
            break
    
    if gene_symbol_lines:
        print("Found references to gene symbols:")
        for line in gene_symbol_lines[:5]:  # Show just first 5 matches
            print(line)
    else:
        print("No explicit gene symbol references found in first 1000 lines")

# Look for alternative annotation files or references in the directory
print("\nChecking for additional annotation files in the directory:")
all_files = os.listdir(in_cohort_dir)
print([f for f in all_files if 'annotation' in f.lower() or 'platform' in f.lower() or 'gpl' in f.lower()])



Gene annotation preview:
Columns in gene annotation: ['ID', 'GB_LIST', 'SPOT_ID', 'seqname', 'RANGE_GB', 'RANGE_STRAND', 'RANGE_START', 'RANGE_STOP', 'total_probes', 'gene_assignment', 'mrna_assignment', 'category']
{'ID': ['2315100', '2315106', '2315109', '2315111', '2315113'], 'GB_LIST': ['NR_024005,NR_034090,NR_024004,AK093685', 'DQ786314', nan, nan, 'DQ786265'], 'SPOT_ID': ['chr1:11884-14409', 'chr1:14760-15198', 'chr1:19408-19712', 'chr1:25142-25532', 'chr1:27563-27813'], 'seqname': ['chr1', 'chr1', 'chr1', 'chr1', 'chr1'], 'RANGE_GB': ['NC_000001.10', 'NC_000001.10', 'NC_000001.10', 'NC_000001.10', 'NC_000001.10'], 'RANGE_STRAND': ['+', '+', '+', '+', '+'], 'RANGE_START': ['11884', '14760', '19408', '25142', '27563'], 'RANGE_STOP': ['14409', '15198', '19712', '25532', '27813'], 'total_probes': ['20', '8', '4', '4', '4'], 'gene_assignment': ['NR_024005 // DDX11L2 // DEAD/H (Asp-Glu-Ala-Asp/His) box polypeptide 11 like 2 // 2q13 // 84771 /// NR_034090 // DDX11L9 // DEAD/H (Asp-Glu

No explicit gene symbol references found in first 1000 lines

Checking for additional annotation files in the directory:
[]


### Step 6: Gene Identifier Mapping

In [7]:
# 1. Identifying which columns to use for mapping
# From the gene annotation preview, we can see:
# - 'ID' column contains the probe identifiers (e.g., '2315100') matching those in gene_data
# - 'gene_assignment' column contains gene symbol information with format like "NR_024005 // DDX11L2 // ..."

print("\nPreparing gene mapping:")
# Define the columns for mapping
probe_id_col = 'ID'
gene_symbol_col = 'gene_assignment'

# 2. Create gene mapping dataframe
mapping_df = get_gene_mapping(gene_annotation, probe_id_col, gene_symbol_col)
print(f"Initial mapping shape: {mapping_df.shape}")

# Preview the mapping DataFrame
print("Preview of mapping dataframe:")
print(preview_df(mapping_df, n=5))

# 3. Apply gene mapping to convert probe-level measurements to gene expression
gene_data = apply_gene_mapping(gene_data, mapping_df)
print(f"Mapped gene data shape: {gene_data.shape}")

# Preview the first few rows and columns of the gene expression data
print("Preview of gene expression data:")
print(gene_data.iloc[:5, :5])

# Save the gene expression data to a CSV file
os.makedirs(os.path.dirname(out_gene_data_file), exist_ok=True)
gene_data.to_csv(out_gene_data_file)
print(f"Gene expression data saved to {out_gene_data_file}")



Preparing gene mapping:


Initial mapping shape: (316481, 2)
Preview of mapping dataframe:
{'ID': ['2315100', '2315106', '2315109', '2315111', '2315113'], 'Gene': ['NR_024005 // DDX11L2 // DEAD/H (Asp-Glu-Ala-Asp/His) box polypeptide 11 like 2 // 2q13 // 84771 /// NR_034090 // DDX11L9 // DEAD/H (Asp-Glu-Ala-Asp/His) box polypeptide 11 like 9 // 15q26.3 // 100288486 /// NR_024004 // DDX11L2 // DEAD/H (Asp-Glu-Ala-Asp/His) box polypeptide 11 like 2 // 2q13 // 84771 /// AK093685 // DDX11L2 // DEAD/H (Asp-Glu-Ala-Asp/His) box polypeptide 11 like 2 // 2q13 // 84771', '---', '---', '---', '---']}


Mapped gene data shape: (48895, 226)
Preview of gene expression data:
      GSM6411059  GSM6411060  GSM6411061  GSM6411062  GSM6411063
Gene                                                            
A-      0.719033    0.599778    0.721831    0.370105    0.443005
A-2     0.089536    0.112220    0.152537    0.030428    0.039532
A-52    1.377630    1.006911    1.287671    1.149916    0.945399
A-E    -0.088865   -0.050165   -0.028029   -0.082610   -0.084426
A-I     0.320277    0.501120    0.308924    0.224898    0.401896


Gene expression data saved to ../../output/preprocess/Prostate_Cancer/gene_data/GSE209954.csv


### Step 7: Data Normalization and Linking

In [8]:
# 1. Normalize gene symbols in the gene expression data using the normalize_gene_symbols_in_index function
print(f"Gene data shape before normalization: {gene_data.shape}")
gene_data = normalize_gene_symbols_in_index(gene_data)
print(f"Gene data shape after normalization: {gene_data.shape}")

# Save the normalized gene expression data
os.makedirs(os.path.dirname(out_gene_data_file), exist_ok=True)
gene_data.to_csv(out_gene_data_file)
print(f"Normalized gene expression data saved to {out_gene_data_file}")

# 2. Load the previously saved clinical data and properly format it
try:
    clinical_data = pd.read_csv(out_clinical_data_file)
    print(f"Loaded clinical data with shape: {clinical_data.shape}")
    
    # Check the column names to understand the structure
    print(f"Clinical data columns: {clinical_data.columns.tolist()}")
    
    # From the previous steps, we know we have race (AAM vs NAAM) as our trait
    # Create a proper clinical dataframe where samples are rows
    # First, set the index to the first column if it's not already set
    if 'Unnamed: 0' in clinical_data.columns:
        clinical_data = clinical_data.set_index('Unnamed: 0')
    
    # Transpose so samples become rows
    clinical_data_t = clinical_data.T
    # The first row contains Prostate_Cancer (our trait) and the second row is Age
    clinical_data_t.columns = [trait, "Age"]
    print(f"Transposed clinical data shape: {clinical_data_t.shape}")
    
    # Check sample overlap between clinical and genetic data
    clinical_samples = set(clinical_data_t.index)
    genetic_samples = set(gene_data.columns)
    print(f"Clinical samples: {len(clinical_samples)}")
    print(f"Genetic samples: {len(genetic_samples)}")
    print(f"Common samples: {len(clinical_samples.intersection(genetic_samples))}")
    
    # Modify the column names in gene_data to match sample IDs in clinical data
    # Extract just the GSM IDs from both datasets if needed
    # For example, if gene_data columns are GSM123456 and clinical has Sample_1
    
    # Transpose gene data to get samples as rows
    gene_data_t = gene_data.T
    
    # Create linked data by adding gene expression data to clinical data
    linked_data = pd.DataFrame(index=gene_data_t.index)
    
    # Add clinical data where available (for matching samples)
    for col in clinical_data_t.columns:
        linked_data[col] = None  # Initialize column
        common_samples = clinical_data_t.index.intersection(linked_data.index)
        linked_data.loc[common_samples, col] = clinical_data_t.loc[common_samples, col]
    
    # Add gene expression data
    for col in gene_data_t.columns:
        linked_data[col] = gene_data_t[col]
    
    print(f"Linked data shape: {linked_data.shape}")
    print(f"Number of non-null trait values: {linked_data[trait].count()}")
    
    # 3. Handle missing values
    if linked_data[trait].count() > 0:
        linked_data_clean = handle_missing_values(linked_data, trait)
        print(f"Cleaned linked data shape: {linked_data_clean.shape}")
        
        # 4. Determine if the trait and demographic features are biased
        if linked_data_clean.shape[0] > 0:
            is_biased, linked_data_clean = judge_and_remove_biased_features(linked_data_clean, trait)
            trait_available = True
        else:
            print("No samples remaining after missing value handling")
            is_biased = True
            trait_available = False
    else:
        print("No valid trait values found in linked data")
        linked_data_clean = linked_data
        is_biased = True
        trait_available = False
    
except Exception as e:
    print(f"Error loading or processing clinical data: {e}")
    print("Falling back to gene data only")
    trait_available = False
    linked_data = gene_data.T
    linked_data_clean = linked_data
    is_biased = True

# 5. Conduct final quality validation
note = "Dataset contains prostate cancer samples from African American Males (AAM=1) and Non-African American Males (NAAM=0). Age information is included as a covariate."

is_usable = validate_and_save_cohort_info(
    is_final=True,
    cohort=cohort,
    info_path=json_path,
    is_gene_available=True,
    is_trait_available=trait_available,
    is_biased=is_biased,
    df=linked_data_clean,
    note=note
)

# 6. Save the linked data if usable
if is_usable:
    os.makedirs(os.path.dirname(out_data_file), exist_ok=True)
    linked_data_clean.to_csv(out_data_file)
    print(f"Linked data saved to {out_data_file}")
else:
    print("Dataset deemed not usable due to quality issues - linked data not saved")

Gene data shape before normalization: (48895, 226)
Gene data shape after normalization: (18418, 226)


Normalized gene expression data saved to ../../output/preprocess/Prostate_Cancer/gene_data/GSE209954.csv
Loaded clinical data with shape: (2, 30)
Clinical data columns: ['Sample_1', 'Sample_2', 'Sample_3', 'Sample_4', 'Sample_5', 'Sample_6', 'Sample_7', 'Sample_8', 'Sample_9', 'Sample_10', 'Sample_11', 'Sample_12', 'Sample_13', 'Sample_14', 'Sample_15', 'Sample_16', 'Sample_17', 'Sample_18', 'Sample_19', 'Sample_20', 'Sample_21', 'Sample_22', 'Sample_23', 'Sample_24', 'Sample_25', 'Sample_26', 'Sample_27', 'Sample_28', 'Sample_29', 'Sample_30']
Transposed clinical data shape: (30, 2)
Clinical samples: 30
Genetic samples: 226
Common samples: 0


/tmp/ipykernel_71239/4069072151.py:56: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  linked_data[col] = gene_data_t[col]
/tmp/ipykernel_71239/4069072151.py:56: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  linked_data[col] = gene_data_t[col]
/tmp/ipykernel_71239/4069072151.py:56: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `n

/tmp/ipykernel_71239/4069072151.py:56: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  linked_data[col] = gene_data_t[col]
/tmp/ipykernel_71239/4069072151.py:56: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  linked_data[col] = gene_data_t[col]
/tmp/ipykernel_71239/4069072151.py:56: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `n

/tmp/ipykernel_71239/4069072151.py:56: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  linked_data[col] = gene_data_t[col]
/tmp/ipykernel_71239/4069072151.py:56: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  linked_data[col] = gene_data_t[col]
/tmp/ipykernel_71239/4069072151.py:56: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `n

...

/tmp/ipykernel_71239/4069072151.py:56: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  linked_data[col] = gene_data_t[col]
/tmp/ipykernel_71239/4069072151.py:56: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  linked_data[col] = gene_data_t[col]
/tmp/ipykernel_71239/4069072151.py:56: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `n

/tmp/ipykernel_71239/4069072151.py:56: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  linked_data[col] = gene_data_t[col]
/tmp/ipykernel_71239/4069072151.py:56: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  linked_data[col] = gene_data_t[col]
/tmp/ipykernel_71239/4069072151.py:56: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `n

/tmp/ipykernel_71239/4069072151.py:56: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  linked_data[col] = gene_data_t[col]
/tmp/ipykernel_71239/4069072151.py:56: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  linked_data[col] = gene_data_t[col]
/tmp/ipykernel_71239/4069072151.py:56: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `n

/tmp/ipykernel_71239/4069072151.py:56: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  linked_data[col] = gene_data_t[col]
/tmp/ipykernel_71239/4069072151.py:56: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  linked_data[col] = gene_data_t[col]
/tmp/ipykernel_71239/4069072151.py:56: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `n

Linked data shape: (226, 18420)
Number of non-null trait values: 0
No valid trait values found in linked data
Dataset deemed not usable due to quality issues - linked data not saved
